In [53]:
import pandas as pd


In [ ]:
game_data = pd.read_csv("data/full_data_v1.1.csv").sort_values(by="id")

In [55]:
preis = game_data["price"]

In [56]:
preis.max()

np.float64(147300.0)

In [57]:
preis[preis == 147300.0]

61504    147300.0
Name: price, dtype: float64

In [58]:
game_data.iloc[61504]

Unnamed: 0                                                                61856
id                                                                      2691920
name                                                              MolCollabo v2
released                                                             2025-02-03
genre                                                                     Indie
categories                    Einzelspieler;Mehrspieler;Unterstützung für Co...
required_age                                                                0.0
feature                                                                     NaN
total_reviews                                                               0.0
positive_reviews                                                            0.0
negative_reviews                                                            0.0
reviews_30_days_total                                                       0.0
reviews_30_days_percentage              

In [ ]:
image_data = pd.read_csv("data/second_additional_info_v1.csv").sort_values(by="id")

In [60]:
image_data.columns

Index(['id', 'image', 'detailed_description', 'short_description'], dtype='object')

In [ ]:
game_data = pd.read_csv("data/full_data_v1.1.csv").sort_values(by="id")

In [62]:
game_data.columns

Index(['Unnamed: 0', 'id', 'name', 'released', 'genre', 'categories',
       'required_age', 'feature', 'total_reviews', 'positive_reviews',
       'negative_reviews', 'reviews_30_days_total',
       'reviews_30_days_percentage', 'tags', 'price'],
      dtype='object')

In [63]:
q3 = game_data["total_reviews"].quantile(0.75)
q1 = game_data["total_reviews"].quantile(0.25)
q2 = game_data["total_reviews"].median()

In [64]:
y  = (game_data["total_reviews"] - q2) / (q3-q1)

In [65]:
y = y.sort_values()

In [66]:
y

85730       -0.194444
85731       -0.194444
85712       -0.194444
85713       -0.194444
85714       -0.194444
             ...     
6387     13465.361111
6388     13465.361111
21       23938.685185
8089     24312.018519
25       84604.500000
Name: total_reviews, Length: 85746, dtype: float64

In [67]:
x = game_data["total_reviews"]

In [68]:
mw = x.mean()

In [69]:
sd = x.std()
sd

np.float64(40967.99453343551)

In [70]:
z_score = (x-mw)/sd

In [71]:
z_score

0        6.144752
1        0.171601
2        0.129324
3        0.032688
4        0.601742
           ...   
85741   -0.045471
85742   -0.045593
85743   -0.045178
85744   -0.045593
85745   -0.045568
Name: total_reviews, Length: 85746, dtype: float64

In [72]:
pr = game_data["positive_reviews"] # positive reviews
nr = game_data["negative_reviews"] # negative reviews
n = game_data["total_reviews"]  # Gesamtreviews für das Spiel
import numpy as np

p = np.where(n>0, pr/n, 0)
SE = np.where(n>0, np.sqrt(p * (1 - p) / n),0)

from scipy.stats import norm

# z-Wert für 95% Konfidenzintervall
alpha = 0.05
z = norm.ppf(1 - alpha/2)  

print(z)  # ca. 1.96

p_lower = p - z*SE



1.959963984540054


In [73]:
wald_intervall_lower_bound = pd.Series(p_lower, name="wald_intervall_lower_bound")

In [74]:
#Agresti Coull-Intervall
k = game_data["positive_reviews"]
n = game_data["total_reviews"]

from scipy.stats import norm

# z-Wert für 95% Konfidenzintervall
alpha = 0.05
z = norm.ppf(1 - alpha/2)

#adjustierten werte: 

k_tilde = k + z**2 / 2
n_tilde = n + z**2
p_tilde = k_tilde/n_tilde
SE_ac = np.sqrt((p_tilde*(1-p_tilde)/n_tilde))


agresti_coull_intervall_lower_bound = p_tilde - z*SE_ac

In [75]:
agresti_coull_intervall_lower_bound  = pd.Series(agresti_coull_intervall_lower_bound, name="agresti_coull_intervall_lower_bound")

In [76]:
#Wilson Interval 
from scipy.stats import norm

# z-Wert für 95% Konfidenzintervall
alpha = 0.05
z = norm.ppf(1 - alpha/2)

k = game_data["positive_reviews"]
n = game_data["total_reviews"]
p_dach = np.where(n>0, k/n, 0)

wilson_lower_bound = np.where(n>0, 
                              1/(1+(z**2/n)) * (p_dach + z**2/(2*n) - z* np.sqrt(
                                ( p_dach* (1-p_dach) / n) + z**2 / (4*n**2)
                              )), 0) 

In [77]:
wilson_lower_bound.min()

np.float64(0.0)

In [79]:
wilson_lower_bound  = pd.Series(wilson_lower_bound, name="wilson_lower_bound")

In [80]:
merge = pd.concat([wald_intervall_lower_bound,agresti_coull_intervall_lower_bound,wilson_lower_bound], axis=1)

In [81]:
merge.head()

wald_intervall_lower_bound  agresti_coull_intervall_lower_bound  \
0                    0.973567                             0.973560   
1                    0.864362                             0.864200   
2                    0.896306                             0.896085   
3                    0.817060                             0.816661   
4                    0.950586                             0.950519   

   wilson_lower_bound  
0            0.973560  
1            0.864201  
2            0.896089  
3            0.816667  
4            0.950520

In [ ]:
from scipy.stats import norm
percentage = k/n
R = percentage.mean()

pr = game_data["positive_reviews"]
nr = game_data["negative_reviews"]
n = game_data["total_reviews"]

w = pr.median()

bayesian_rating = (R*w + pr)/(w+n)



In [116]:
bayesian_rating = pd.Series(bayesian_rating, name="bayesian_rating")

In [117]:
merge = pd.concat([merge, bayesian_rating], axis=1)

In [118]:
merge.head()

wald_intervall_lower_bound  agresti_coull_intervall_lower_bound  \
0                    0.973567                             0.973560   
1                    0.864362                             0.864200   
2                    0.896306                             0.896085   
3                    0.817060                             0.816661   
4                    0.950586                             0.950519   

   wilson_lower_bound  bayesian_rating  
0            0.973560         0.974172  
1            0.864201         0.871152  
2            0.896089         0.902875  
3            0.816667         0.829800  
4            0.950520         0.953024

In [119]:
merge = pd.concat([merge, pr,nr, n], axis=1)

In [120]:
merge.tail()

wald_intervall_lower_bound  agresti_coull_intervall_lower_bound  \
85741                    0.449391                         3.596312e-01   
85742                    0.000000                         5.551115e-17   
85743                    0.489286                         4.657430e-01   
85744                    0.000000                         5.551115e-17   
85745                    1.000000                         1.674995e-01   

       wilson_lower_bound  bayesian_rating  positive_reviews  \
85741            0.375535         0.783188               4.0   
85742            0.000000         0.777934               0.0   
85743            0.468669         0.740817              12.0   
85744            0.000000         0.777934               0.0   
85745            0.206549         0.790997               1.0   

       negative_reviews  total_reviews  
85741               1.0            5.0  
85742               0.0            0.0  
85743               5.0           17.0  
85744               0.0            0.0  
85745               0.0            1.0

In [123]:
merge.head()

wald_intervall_lower_bound  agresti_coull_intervall_lower_bound  \
0                    0.973567                             0.973560   
1                    0.864362                             0.864200   
2                    0.896306                             0.896085   
3                    0.817060                             0.816661   
4                    0.950586                             0.950519   

   wilson_lower_bound  bayesian_rating  positive_reviews  negative_reviews  \
0            0.973560         0.974172          247059.0            6547.0   
1            0.864201         0.871152            7753.0            1145.0   
2            0.896089         0.902875            6472.0             694.0   
3            0.816667         0.829800            2662.0             545.0   
4            0.950520         0.953024           25277.0            1243.0   

   total_reviews  
0       253606.0  
1         8898.0  
2         7166.0  
3         3207.0  
4        26520.0

In [ ]:
import plotly.express as px

df = merge.iloc[:, 0:4].melt(var_name='method', value_name='value')

px.histogram(df, x='value', color='method', barmode='overlay')



ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'bingroup': 'x',
              'hovertemplate': 'method=wald_intervall_lower_bound<br>value=%{x}<br>count=%{y}<extra></extra>',
              'legendgroup': 'wald_intervall_lower_bound',
              'marker': {'color': '#636efa', 'opacity': 0.5, 'pattern': {'shape': ''}},
              'name': 'wald_intervall_lower_bound',
              'orientation': 'v',
              'showlegend': True,
              'type': 'histogram',
              'x': {'bdata': ('wlhDUHYn7z9+Oqh82qjrP8CwUYSKru' ... '546XdQ3z8AAAAAAAAAAAAAAAAAAPA/'),
                    'dtype': 'f8'},
              'xaxis': 'x',
              'yaxis': 'y'},
             {'bingroup': 'x',
              'hovertemplate': ('method=agresti_coull_intervall' ... '}<br>count=%{y}<extra></extra>'),
              'legendgroup': 'agresti_coull_intervall_lower_bound',
              'marker': {'color': '#EF553B', 'opacity': 0.5, 'pattern': {'shape': ''}},
              'name': 'agresti_coull_intervall_lower_bound',
              'orientation': 'v',
              'showlegend': True,
              'type': 'histogram',
              'x': {'bdata': ('o8LPFWcn7z+nPRjbhafrP5sx7xe7rO' ... '9S0rvO3T8AAAAAAACQPFKOHYafcMU/'),
                    'dtype': 'f8'},
              'xaxis': 'x',
              'yaxis': 'y'},
             {'bingroup': 'x',
              'hovertemplate': 'method=wilson_lower_bound<br>value=%{x}<br>count=%{y}<extra></extra>',
              'legendgroup': 'wilson_lower_bound',
              'marker': {'color': '#00cc96', 'opacity': 0.5, 'pattern': {'shape': ''}},
              'name': 'wilson_lower_bound',
              'orientation': 'v',
              'showlegend': True,
              'type': 'histogram',
              'x': {'bdata': ('XP8+LGcn7z+WVSO5iafrP8JpHjvCrO' ... 'fS1qv+3T8AAAAAAAAAAG93ITs1cMo/'),
                    'dtype': 'f8'},
              'xaxis': 'x',
              'yaxis': 'y'},
             {'bingroup': 'x',
              'hovertemplate': 'method=bayesian_rating<br>value=%{x}<br>count=%{y}<extra></extra>',
              'legendgroup': 'bayesian_rating',
              'marker': {'color': '#ab63fa', 'opacity': 0.5, 'pattern': {'shape': ''}},
              'name': 'bayesian_rating',
              'orientation': 'v',
              'showlegend': True,
              'type': 'histogram',
              'x': {'bdata': ('4O2JuWos7z9Hu2exeeDrPz6WQLtZ5O' ... 'DY8sS05z87cN801uToP+y0O6rYT+k/'),
                    'dtype': 'f8'},
              'xaxis': 'x',
              'yaxis': 'y'}],
    'layout': {'barmode': 'overlay',
               'legend': {'title': {'text': 'method'}, 'tracegroupgap': 0},
               'margin': {'t': 60},
               'template': '...',
               'xaxis': {'anchor': 'y', 'domain': [0.0, 1.0], 'title': {'text': 'value'}},
               'yaxis': {'anchor': 'x', 'domain': [0.0, 1.0], 'title': {'text': 'count'}}}
})